In [1]:
import numpy as np
import tensorflow as tf

/home/naomichi/venvs/python3.6/lib/python3.6/importlib/_bootstrap.py:205: RuntimeWarning: compiletime version 3.5 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.6
  return f(*args, **kwds)


In [2]:
tf.logging.set_verbosity(tf.logging.INFO)

In [24]:
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    input_layer = tf.reshape(features['x'], [-1, 28, 28, 1])
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding='same',
        activation=tf.nn.relu,
    )
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)
    
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding='same',
        activation=tf.nn.relu,
    )
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)
    
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(
        inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    
    logits = tf.layers.dense(inputs=dropout, units=10)
    
    predictions = {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    
    onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
    loss = tf.losses.softmax_cross_entropy(onehot_labels=onehot_labels, logits=logits)
    
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(loss=loss, global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
    
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions['classes'])
    }
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [25]:
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [26]:
mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7fd5336d58d0>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


In [27]:
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

In [37]:
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(input_fn=train_input_fn, steps=20000, hooks=[logging_hook])

INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Saving checkpoints for 20001 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[ 0.00022817  0.00000086  0.00012388  0.00017194  0.93645895  0.00283372
   0.00299721  0.00065681  0.00096694  0.05556151]
 [ 0.00002566  0.00001158  0.00549307  0.00008184  0.00447073  0.00160984
   0.00006124  0.00219448  0.00030793  0.9857437 ]
 [ 0.00000001  0.0000068   0.00001076  0.00799651  0.00004456  0.00000048
   0.          0.89750963  0.00005506  0.09437614]
 [ 0.00000061  0.00000001  0.00000002  0.00000022  0.0000036   0.00000115
   0.          0.99988651  0.00000006  0.00010781]
 [ 0.00001451  0.99785006  0.00036465  0.00009145  0.00027632  0.00000525
   0.00031283  0.00021023  0.00078663  0.00008815]
 [ 0.00000041  0.00010522  0.00022873  0.00198412  0.00000915  0.00000326
   0.          0.99009484  0.00004397  0.00753036]
 [ 

INFO:tensorflow:loss = 0.122094, step = 20001
INFO:tensorflow:probabilities = [[ 0.00023856  0.98868853  0.00049478  0.0002166   0.00099172  0.00019666
   0.00081402  0.00036388  0.00764232  0.00035292]
 [ 0.00029149  0.00012752  0.00071198  0.00386748  0.0000837   0.00568319
   0.00000885  0.00013248  0.97998911  0.00910417]
 [ 0.99989188  0.0000004   0.00001114  0.00000136  0.00000001  0.00006481
   0.00000028  0.00000326  0.00001226  0.00001468]
 [ 0.00011183  0.00000126  0.0001271   0.00027977  0.00000548  0.00005848
   0.00000013  0.99826187  0.0000021   0.00115207]
 [ 0.00002523  0.          0.0000003   0.00217635  0.00000148  0.99657083
   0.00000529  0.00000247  0.00008566  0.00113246]
 [ 0.00001791  0.00000001  0.00035482  0.00000226  0.00001733  0.00002395
   0.00000639  0.00004286  0.99833316  0.00120126]
 [ 0.00000032  0.0168536   0.97622401  0.00686144  0.00001286  0.00001766
   0.00000819  0.00000794  0.00001326  0.00000069]
 [ 0.07589266  0.49252909  0.00159373  0.000444

INFO:tensorflow:global_step/sec: 150.503
INFO:tensorflow:probabilities = [[ 0.00000703  0.00000381  0.00177009  0.00095276  0.00000004  0.00000187
   0.          0.99648154  0.00000179  0.00078108]
 [ 0.01595915  0.00206426  0.00073594  0.00143745  0.00062198  0.01365821
   0.96367204  0.00000262  0.00181022  0.00003806]
 [ 0.17911309  0.02086072  0.03780908  0.6559785   0.00005095  0.07613875
   0.00019217  0.01214675  0.00667918  0.01103084]
 [ 0.00014522  0.00020763  0.01207075  0.0000861   0.00025802  0.00627154
   0.01825292  0.00000361  0.96262228  0.00008193]
 [ 0.0000014   0.00001467  0.00004548  0.97991973  0.00005994  0.01796882
   0.00000909  0.00006811  0.00150173  0.00041099]
 [ 0.00000996  0.00000786  0.00008528  0.99692589  0.00002108  0.00040767
   0.00000021  0.00000443  0.00127205  0.0012655 ]
 [ 0.00001272  0.98879749  0.00024984  0.00008088  0.00020762  0.00003219
   0.00445228  0.00003519  0.00611972  0.00001205]
 [ 0.0000094   0.0003355   0.9977386   0.00166604  0

INFO:tensorflow:loss = 0.0899455, step = 20101 (0.665 sec)
INFO:tensorflow:probabilities = [[ 0.00004936  0.00010077  0.97733718  0.01930555  0.00000132  0.0000052
   0.00000049  0.00248035  0.000646    0.00007375]
 [ 0.0000248   0.99748355  0.00031001  0.00013476  0.00018586  0.000051
   0.00003077  0.00083775  0.00091348  0.00002808]
 [ 0.00200005  0.02870795  0.16158682  0.03307647  0.00532982  0.00029754
   0.00115953  0.0088447   0.75174743  0.00724967]
 [ 0.00004137  0.00000002  0.00010838  0.00016323  0.00002501  0.00019169
   0.00001464  0.00000004  0.99706751  0.00238811]
 [ 0.00000656  0.05876685  0.93984604  0.00110594  0.00000039  0.00001183
   0.0000712   0.00000305  0.00018812  0.00000004]
 [ 0.00219845  0.00032659  0.00028108  0.12965633  0.00044861  0.00187084
   0.00000255  0.00033189  0.74948388  0.1153998 ]
 [ 0.00000006  0.00031241  0.99945921  0.00009824  0.00000029  0.00000038
   0.00000002  0.00001507  0.00011317  0.00000113]
 [ 0.00003258  0.99603432  0.00030764

INFO:tensorflow:global_step/sec: 160.887
INFO:tensorflow:probabilities = [[ 0.00063651  0.99149454  0.00131257  0.00119853  0.00019864  0.00002795
   0.0000591   0.00325852  0.00163413  0.00017953]
 [ 0.00005105  0.00000033  0.00011972  0.00002056  0.00000183  0.00004326
   0.00000794  0.00000035  0.9997009   0.00005408]
 [ 0.0003165   0.00287176  0.97830737  0.00755726  0.000139    0.0000544
   0.00011762  0.00001033  0.0102306   0.00039518]
 [ 0.00007065  0.00000068  0.00024282  0.00070841  0.00075299  0.0362961
   0.00002621  0.00396539  0.05367229  0.90426445]
 [ 0.00000249  0.0000168   0.00003238  0.00021251  0.02361209  0.00000697
   0.00000096  0.00388471  0.0003096   0.9719215 ]
 [ 0.00001998  0.9969036   0.00008832  0.00015148  0.00042292  0.00003674
   0.0004983   0.00014814  0.00162209  0.0001085 ]
 [ 0.0000111   0.00006204  0.00647846  0.00191275  0.00682811  0.0002527
   0.00000728  0.28993249  0.00077653  0.69373852]
 [ 0.00007028  0.00231682  0.00134225  0.00313611  0.03

...

INFO:tensorflow:global_step/sec: 159.858
INFO:tensorflow:probabilities = [[ 0.93729609  0.00000067  0.05941008  0.00001142  0.00000288  0.0000002
   0.00000042  0.00083313  0.00000491  0.00244019]
 [ 0.00000858  0.00000038  0.00000734  0.00087943  0.00088757  0.00029135
   0.00000001  0.05504486  0.00024571  0.9426347 ]
 [ 0.00054808  0.00000465  0.00001309  0.00004111  0.00005966  0.00039543
   0.99893349  0.00000001  0.00000429  0.00000007]
 [ 0.00000049  0.00000048  0.0000931   0.00001457  0.99883646  0.00010381
   0.00000109  0.00010864  0.00000238  0.00083898]
 [ 0.00000705  0.99742812  0.00091496  0.0000139   0.00092101  0.00000119
   0.00000437  0.00054421  0.00015397  0.00001117]
 [ 0.          0.00014006  0.99981886  0.00000219  0.00000001  0.          0.
   0.          0.00003892  0.        ]
 [ 0.99849534  0.00000254  0.00071886  0.00001293  0.00002302  0.00000023
   0.00002379  0.00001061  0.00071108  0.00000168]
 [ 0.00004012  0.00000008  0.00010655  0.00001687  0.00000007

INFO:tensorflow:loss = 0.0375928, step = 39801 (0.627 sec)
INFO:tensorflow:probabilities = [[ 0.00000064  0.          0.00000002  0.00001862  0.00003977  0.00000586
   0.          0.00001255  0.00002078  0.99990177]
 [ 0.00002685  0.00000297  0.0002092   0.00000033  0.00000438  0.00229606
   0.99472189  0.          0.00273832  0.00000006]
 [ 0.00000005  0.00000003  0.00000001  0.00001728  0.0017822   0.00000174
   0.00000001  0.00000066  0.00000315  0.99819499]
 [ 0.00000032  0.00000118  0.00122415  0.00467662  0.00000026  0.00028488
   0.00000081  0.00000112  0.99378973  0.0000208 ]
 [ 0.00055466  0.00000797  0.00001383  0.00001536  0.00006643  0.01147199
   0.98731494  0.0000015   0.00054112  0.00001214]
 [ 0.00000117  0.0000002   0.00001261  0.00000013  0.00000022  0.00000229
   0.99998188  0.          0.00000156  0.        ]
 [ 0.00001335  0.99851078  0.00045122  0.00002066  0.00002885  0.00003967
   0.00038572  0.00007897  0.00046655  0.00000425]
 [ 0.00000018  0.00000001  0.00000

INFO:tensorflow:global_step/sec: 159.955
INFO:tensorflow:probabilities = [[ 0.00000153  0.00000001  0.99972838  0.00006402  0.          0.
   0.00000006  0.00000016  0.00020581  0.00000002]
 [ 0.00021602  0.9916836   0.00001163  0.00003161  0.00000829  0.000012
   0.0000131   0.00178207  0.00622288  0.00001884]
 [ 0.06168625  0.01172986  0.00897111  0.89377356  0.00000635  0.0109688
   0.00008567  0.00308643  0.00117453  0.00851745]
 [ 0.0000189   0.00000114  0.00000028  0.00001116  0.00000001  0.99994814
   0.00000164  0.00000101  0.00001775  0.00000001]
 [ 0.00003661  0.00003205  0.01153701  0.00085175  0.00000192  0.02684243
   0.00019759  0.00001535  0.96017593  0.0003094 ]
 [ 0.0000036   0.00000036  0.0000676   0.00000003  0.0002257   0.00000083
   0.99969983  0.00000004  0.00000188  0.00000018]
 [ 0.00000001  0.          0.00000048  0.00000083  0.00000001  0.          0.
   0.99999738  0.00000025  0.00000112]
 [ 0.00000023  0.02552777  0.97426105  0.00012978  0.          0.000000

INFO:tensorflow:loss = 0.0659662, step = 39901 (0.624 sec)
INFO:tensorflow:probabilities = [[ 0.00000013  0.00000002  0.000001    0.00008456  0.0000006   0.99527788
   0.00007778  0.          0.00448943  0.00006861]
 [ 0.          0.          0.          0.          0.99999309  0.00000001
   0.          0.00000007  0.00000011  0.00000671]
 [ 0.00000156  0.00000024  0.00000499  0.00010523  0.00204943  0.00005404
   0.00000098  0.00038596  0.00005257  0.99734503]
 [ 0.00005135  0.00023302  0.00007742  0.00004529  0.00061055  0.00012606
   0.99877912  0.00000155  0.00007519  0.00000043]
 [ 0.          0.00000016  0.00000028  0.9995876   0.0000001   0.00007697
   0.          0.00000065  0.00005229  0.00028203]
 [ 0.00070125  0.0665685   0.00400312  0.00726097  0.00002183  0.00034985
   0.00001654  0.00076946  0.9201057   0.00020277]
 [ 0.00001774  0.00002269  0.00005178  0.0225109   0.00001355  0.9345119
   0.00044928  0.00000022  0.03740408  0.00501773]
 [ 0.00000011  0.00000037  0.000003

INFO:tensorflow:Saving checkpoints for 40000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.151406.


In [38]:
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Starting evaluation at 2017-12-21-07:46:45
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-40000
INFO:tensorflow:Finished evaluation at 2017-12-21-07:46:46
INFO:tensorflow:Saving dict for global step 40000: accuracy = 0.981, global_step = 40000, loss = 0.0593797
{'accuracy': 0.98100001, 'loss': 0.059379715, 'global_step': 40000}
